# Vamos a jugar un poco con python y Pandas.

Me bajé, del repositorio de datos de la ciudad de Buenos Aires, un listado completo de universidades con sede en CABA y sus unidades académicas: https://data.buenosaires.gob.ar/dataset/universidades

Vamos a ver qué podemos hacer con eso...

Primero vamos a importar pandas, para procesar el CSV como dataset

In [1]:
import pandas as pd

Vamos a levantar el CSV y a revisar qué tiene...

In [2]:
universidades_data = pd.read_csv('./universidades.csv')
universidades_data.head()

regimen                                         universida  univ_c  \
0  Privado  FLACSO (Facultad Latinoamericana de Ciencias S...       1   
1  Privado              Instituto Tecnológico de Buenos Aires       2   
2  Privado              Instituto Tecnológico de Buenos Aires       2   
3  Privado              Instituto Tecnológico de Buenos Aires       2   
4  Privado              Instituto Tecnológico de Buenos Aires       2   

                      unidad_aca  unac_c  anexo_c  unicue   cui  \
0                      Rectorado       1        0  100100  2546   
1                      Rectorado       1        0  200100  2456   
2  Departamento de Investigación       7        0  200700  2456   
3                Área de Energía      40        0  204000  2456   
4  Departamento de Bioingeniería      87        0  208700  2456   

                    telef        fax    ...              direccion_norm  \
0  5238-9339 (C)5238-9300  4375-1373    ...                Ayacucho 555   
1   63934813 [C]6393-4810  6393-4813    ...      Av. Eduardo Madero 399   
2               6393-4869  6393-4869    ...      Av. Eduardo Madero 399   
3               6393-4870  6393-4870    ...      Av. Eduardo Madero 399   
4               6393-4893  6393-4893    ...      Av. Eduardo Madero 399   

                 calle altura                                     WKT_gkba  \
0            Ayacucho     555  POINT (-58.3953412190814 -34.6026584750106)   
1  Av. Eduardo Madero     399  POINT (-58.3678488464698 -34.6031162314776)   
2  Av. Eduardo Madero     399  POINT (-58.3678488464698 -34.6031162314776)   
3  Av. Eduardo Madero     399  POINT (-58.3678488464698 -34.6031162314776)   
4  Av. Eduardo Madero     399  POINT (-58.3678488464698 -34.6031162314776)   

          barrio    comuna codigo_postal  codigo_postal_argentino       long  \
0      Balvanera  Comuna 3        1026.0                 C1026AAC -58.395341   
1  Puerto Madero  Comuna 1        1106.0                 C1106ACD -58.367849   
2  Puerto Madero  Comuna 1        1106.0                 C1106ACD -58.367849   
3  Puerto Madero  Comuna 1        1106.0                 C1106ACD -58.367849   
4  Puerto Madero  Comuna 1        1106.0                 C1106ACD -58.367849   

         lat  
0 -34.602658  
1 -34.603116  
2 -34.603116  
3 -34.603116  
4 -34.603116  

[5 rows x 21 columns]

Para romper los huevos, veamos de qué tipo es el listado (dataframe, obvio)

In [3]:
type(universidades_data)

pandas.core.frame.DataFrame

Dado que cada universidad tiene muchas sedes, vamos a ver dónde tienen sus rectorados

In [4]:
rectorados = universidades_data[universidades_data['unidad_aca'] == 'Rectorado']
print(rectorados)

     regimen                                         universida  univ_c  \
0    Privado  FLACSO (Facultad Latinoamericana de Ciencias S...       1   
1    Privado              Instituto Tecnológico de Buenos Aires       2   
28   Privado                      Instituto Universitario CEMIC       4   
31   Privado  Instituto Universitario de Ciencias de la Salu...       5   
33   Público    Instituto Universitario de Gendarmería Nacional       6   
35   Público  Instituto Universitario de la Policía Federal ...       7   
53   Privado  Instituto Universitario de Salud Mental de la ...       8   
59   Público      Instituto Universitario de Seguridad Marítima       9   
61   Público  Instituto Universitario del Ejército "Mayor Fr...      10   
64   Privado  Instituto Universitario Escuela Argentina de N...      11   
72   Privado  Instituto Universitario Escuela de Medicina de...      12   
81   Privado  Instituto Universitario Escuela Superior de Ec...      13   
88   Privado             

Ya que estamos jugando, vamos a ver cuáles son las universidades

In [6]:
universidades = universidades_data['universida'].unique()

51

Ahora voy a jugar con folium, una librería que encontré que puede servir para mostrar información geolocalizada (el CSV tiene información de latitud y longitud)

# Let's map it up!


Le digo a folium que me cree un mapa, centrado en CABA, y con un toque de zoom para ver bien la ciudad. 
También voy a iterar sobre el listado de universidades, para marcar en el mapa donde están las distintas sedes. Pongo circulitos para las sedes. Y luego haré lo mismo con los rectorados, para contrastar donde tienen los rectorados las distintas universidades. Pongo marcadores típicos para los rectorados

In [14]:
import folium

map_osm = folium.Map(location=[-34.5941696,-58.4583627], zoom_start=12)

universidades_data.apply(lambda row:folium.CircleMarker(location=[row["lat"], 
                                                  row["long"]]).add_to(map_osm),
         axis=1)
universidades_data.apply(lambda row:folium.CircleMarker(location=[row["lat"], 
                                                  row["long"]]).add_to(map_osm),
         axis=1)
rectorados.apply(lambda row:folium.Marker(location=[row["lat"], 
                                                  row["long"]]).add_to(map_osm),
         axis=1)
map_osm

# Jugando con distancias

Ahora vamos a meterle más onda al mapa.
Asumo que el CSV no está ordenado por Universidad, así que no puedo hacer un corte de control

Recordar que:
- universidades : tiene la lista de todas las universidades
- universidades_data: tiene todos los datos
- rectorados: tiene los datos de todos los rectorados

Voy a intentar dibujar una linea entre cada sede y su rectorado

In [210]:
for each_universidad in universidades:
  sedes_filter = universidades_data['universida'] == each_universidad
  sedes = universidades_data[sedes_filter]
    
  #me quedo con la localizacion de todas las sedes de each_universidad  
  sedes_loc = sedes[['lat','long']]
  
  # y, del listado de sedes, me quedo con la localizacion del rectorado 
  rectorado = sedes[ sedes['unidad_aca'] == 'Rectorado']  
  rectorado_loc = rectorado[['lat','long']].values #uso values para transformar el dataframe en array plano
  sedes_array = sedes_loc.values 

  print("------------------",each_universidad)

  for sede in sedes_array:
        points = []
        if (len(rectorado_loc) > 0):  #hay universidades que no tienen rectorado :-( 
            points = [ [sede[0],sede[1]] ]  
            points.append( [ rectorado_loc[0][0],rectorado_loc[0][1]] )
            #points tiene un vector con dos puntos: el rectorado y cada sede 
            folium.PolyLine(points,color="black", weight=25, opacity=1).add_to(map_osm)
            print(sede)
            #print(points)


------------------ FLACSO (Facultad Latinoamericana de Ciencias Sociales)
[-34.60265848 -58.39534122]
------------------ Instituto Tecnológico de Buenos Aires
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
[-34.60311623 -58.36784885]
------------------ Instituto Universitario Aeronáutico
------------------ Instituto Universitario CEMIC
[-34.55493718 -58.49488438]
[-34.55493718 -58.49488438]
[-34.5568

[-34.59401852 -58.40066309]
[-34.59721633 -58.41591987]
[-34.59507291 -58.41461861]
[-34.59721633 -58.41591987]
[-34.59908952 -58.40587312]
[-34.59721633 -58.41591987]
------------------ Universidad de San Andrés
------------------ Universidad del CEMA
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
[-34.5986727  -58.37236042]
------------------ Universidad del Cine
[-34.61674921 -58.3708578 ]
[-34.61674921 -58.3708578 ]
[-34.61674921 -58.3708578 ]
------------------ Universidad del Museo Social Argentino
[-34.60416797 -58.39122069]
[-34.60416797 -58.39122069]
[-34.60416797 -58.39122069]
[-34.

In [211]:
map_osm